In [ ]:
import math
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.patches import Ellipse
import matplotlib.transforms as transforms

from scipy.stats import multivariate_normal

import sklearn
from sklearn.cluster import KMeans
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler

In [ ]:
def data_generator(cluster_nums, cluster_means, cluster_var):
    data = []
    for num, mu, var in zip(cluster_nums, cluster_means, cluster_var):
        data += [np.random.multivariate_normal(mu, np.diag(var), num)]
    data = np.vstack(data)
    return data

mus= [[-6.1, 3.8],[-5.9, -4.2], [6, 0.1]]
vs = [[1, 3],[2, 2],[6, 2]]

X = data_generator(cluster_nums=[50,50,50],
                   cluster_means=mus,
                   cluster_var=vs)

def confidence_ellipse(mu, cov, ax, nstd=3.0, **kwargs):
    def eigsorted(cov):
        vals, vecs = np.linalg.eigh(cov)
        order = vals.argsort()[::-1]
        return vals[order], vecs[:,order]
    if ax is None:
        ax = plt.gca()
    vals, vecs = eigsorted(cov)
    theta = np.degrees(np.arctan2(*vecs[:,0][::-1]))
    width, height = 2 * nstd * np.sqrt(vals)
    ellip = Ellipse(xy=mu, width=width, height=height, angle=theta, facecolor="none", **kwargs)
    ax.add_artist(ellip)
    return ellip

ax = plt.axes()
plt.scatter(X[:, 0], X[:, 1])

for j in range(len(mus)):
    confidence_ellipse(mus[j], np.diag(vs[j]), ax, edgecolor="r")

plt.show()

In [ ]:
def Tk(k, a=0, b=-1, c=1, r=1):
    kappa = (k+r*c)/r
    return 1 + a**kappa + b*np.sin(kappa)/kappa

x = np.arange(1,1000)
plt.plot(x, Tk(x))

In [ ]:
class GaussianMixture():

    def __init__(self, n_components):
        """Inits the GaussianMixture class by setting n_components and n_iter"""
        self.n_components = n_components
        
    
    def kmeans_init(self, X):
        n = X.shape[0]
        d = X.shape[1]
        m = self.n_components

        kms = KMeans(n_clusters=m)
        preds = kms.fit_predict(X)
        
        # sort X by clusters predicted from kmeans
        x_comp = [[] for _ in range(m)]
        for i,pred in enumerate(preds):
            x_comp[pred].append(X[i])
        x_comp = [np.array(x) for x in x_comp]
        
        # compute prior, mean and variance of each cluster 
        alpha = np.zeros(m)
        mu = np.zeros((m, d))
        sigma = np.zeros((m, d, d))
        for i,x in enumerate(x_comp):
            alpha[i] = x.shape[0] / n
            mu[i] = np.mean(x)
            sigma[i] = np.cov(x.T)

        return alpha, mu, sigma

    # Appendix B.1 of the paper
    def fit_em(self, X, n_iter):
        n = X.shape[0]
        d = X.shape[1]
        m = self.n_components
        
        # init with KMeans
        alpha, mu, sigma = self.kmeans_init(X)
        
        # EM loop
        for k in range(n_iter):

            # Expectation
            tau = np.zeros((m, n))
            for j in range(m):
                tau[j] = alpha[j] * multivariate_normal.pdf(X, mu[j], sigma[j])
            tau /= tau.sum(axis=0)
            llikelihood = np.sum(np.log(np.sum(tau, axis=0)))

            # Maximization
            a = np.sum(tau, axis=1)
            alpha = a / np.sum(a)

            mu = np.sum(tau[:,:,None]*X, axis=1) / a[:, None]

            Xm = X - mu[:,None]
            cov = Xm[:,:,:,None] * Xm[:,:,None,:]
            sigma = np.sum(tau[:,:,None,None]*cov, axis=1) / a[:, None,None] + np.eye(d) * 1e-8 # the np.eye 1e-8 prevents some numerical issues
            
        self.alpha = alpha
        self.mu = mu
        self.sigma = sigma
        self.tau = tau

        return np.argmax(tau, axis=0)


    # Appendix B.2 of the paper
    def fit_saem(self, X, n_iter, params):
        n = X.shape[0]
        d = X.shape[1]
        m = self.n_components

        if 'burnin' in params and 'alpha_burnin' in params:
            burnin, alpha_burnin = params['burnin'], params['alpha_burnin']
        else:
            raise Exception("Params must contain: {'burnin': int, 'alpha_burnin': float}")

        # init with KMeans
        alpha, mu, sigma = self.kmeans_init(X)

        # init the sufficient statistics
        S1 = np.zeros(m)
        S2 = np.zeros((m,d))
        S3 = np.zeros((m,d,d))

        # SAEM loop
        np.random.seed(42)
        for k in range(n_iter):

            # Simulation
            ## compute tau 
            tau = np.zeros((m, n))
            for j in range(m):
                tau[j] = alpha[j] * multivariate_normal.pdf(X, mu[j], sigma[j])
            
            ## compute distribution
            tau /= tau.sum(axis=0)
            llikelihood = np.sum(np.log(np.sum(tau, axis=0)))

            ## simulate latent variables
            z = np.zeros(n, dtype=int)
            for i in range(n):
                z[i] = np.random.choice(range(m), p = tau[:,i])

            # Stochastic Approximation
            gamma = 1 if k <= burnin else (k-burnin)**(-alpha_burnin)
            S1_new = np.zeros(m)
            S2_new = np.zeros((m,d))
            S3_new = np.zeros((m,d,d))
            for i in range(n):
                S1_new[z[i]] += 1
                S2_new[z[i]] += X[i]
                S3_new[z[i]] += X[i, None] * X[i,None].T
            S1 = S1 + gamma*(S1_new-S1)
            S2 = S2 + gamma*(S2_new-S2)
            S3 = S3 + gamma*(S3_new-S3)

            # Maximization
            alpha = S1/n
            mu = S2 / S1[:,None]
            sigma = (S3-S2[:,:,None]*mu[:,None,:]) / S1[:,None,None]
            
        self.alpha = alpha
        self.mu = mu
        self.sigma = sigma
        self.tau = tau

        return np.argmax(tau, axis=0)

    # Appendix B.3 of the paper
    def fit_temp_saem(self, X, n_iter, params):
        n = X.shape[0]
        d = X.shape[1]
        m = self.n_components

        if 'burnin' in params and 'alpha_burnin' in params:
            burnin, alpha_burnin = params['burnin'], params['alpha_burnin']
        else:
            raise Exception("Params must contain: {'burnin': int, 'alpha_burnin': float}")

        if 'decreasing_rate' in params and 'amplitude_rate' in params and 'scaling' in params and 'delay' in params:
            decreasing_rate = params['decreasing_rate']
            amplitude_rate = params['amplitude_rate']
            scaling = params['scaling']
            delay = params['delay']
        else:
            raise Exception("Params must contain: {'decreasing_rate', 'amplitude_rate', 'scaling', 'delay'}")
        def Tk(k):
            kappa = (k+scaling*delay)/scaling
            return 1 + decreasing_rate**kappa + amplitude_rate*np.sin(kappa)/kappa

        # init with KMeans
        alpha, mu, sigma = self.kmeans_init(X)

        # init the sufficient statistics
        S1 = np.zeros(m)
        S2 = np.zeros((m,d))
        S3 = np.zeros((m,d,d))

        # SAEM loop
        np.random.seed(42)
        for k in range(n_iter):

            # Simulation
            ## compute tau 
            tau = np.zeros((m, n))
            for j in range(m):
                tau[j] = alpha[j] * multivariate_normal.pdf(X, mu[j], sigma[j])
            
            ## compute tempered distribution
            T = Tk(k)
            tau = tau**(1/T)
            tau /= tau.sum(axis=0)
            llikelihood = np.sum(np.log(np.sum(tau, axis=0)))

            ## simulate latent variables
            z = np.zeros(n, dtype=int)
            for i in range(n):
                z[i] = np.random.choice(range(m), p = tau[:,i])

            # Stochastic Approximation
            gamma = 1 if k <= burnin else (k-burnin)**(-alpha_burnin)
            S1_new = np.zeros(m)
            S2_new = np.zeros((m,d))
            S3_new = np.zeros((m,d,d))
            for i in range(n):
                S1_new[z[i]] += 1
                S2_new[z[i]] += X[i]
                S3_new[z[i]] += X[i, None] * X[i,None].T
            S1 = S1 + gamma*(S1_new-S1)
            S2 = S2 + gamma*(S2_new-S2)
            S3 = S3 + gamma*(S3_new-S3)

            # Maximization
            alpha = S1/n
            mu = S2 / S1[:,None]
            sigma = (S3-S2[:,:,None]*mu[:,None,:]) / S1[:,None,None]
            
        self.alpha = alpha
        self.mu = mu
        self.sigma = sigma
        self.tau = tau

        return np.argmax(tau, axis=0)


In [ ]:
gmm = GaussianMixture(n_components=3)
# params_saem = {'burnin': 10, 'alpha_burnin': 0.8}
# pred_gmm = gmm.fit_saem(X, n_iter= 100, params = params_saem)
params_temp_saem = {'burnin': 10, 'alpha_burnin': 0.8, 
                    'decreasing_rate': 0.0, 'amplitude_rate': -1, 'scaling': 1, 'delay': 1}
pred_gmm = gmm.fit_temp_saem(X, n_iter= 100, params = params_temp_saem)

In [ ]:
ax = plt.axes()
plt.scatter(X[:, 0], X[:, 1], c=pred_gmm)
plt.suptitle('GMM clusters')

for j in range(len(gmm.mu)):
    confidence_ellipse(gmm.mu[j], gmm.sigma[j], ax, edgecolor="r")
for j in range(len(gmm.mu)):
    confidence_ellipse(mus[j], np.diag(vs[j]), ax, edgecolor="g")

plt.show()